### Premissas:
- Nome: dim_calendario
- Descrição da tabela: Tabela composta por variáveis qualitativas de tempo.
- Tipo: SCD-1

In [0]:
# Importa bibliotecas
from pyspark.sql.types import StructType, StructField, IntegerType, FloatType, StringType, TimestampType, LongType
from pyspark.sql.functions import *
from datetime import datetime

In [0]:
# Funçõe de depara e traduções

# Mapeamento de meses em inglês para português
meses_pt_br = {
    'January': 'Janeiro', 'February': 'Fevereiro', 'March': 'Março',
    'April': 'Abril', 'May': 'Maio', 'June': 'Junho',
    'July': 'Julho', 'August': 'Agosto', 'September': 'Setembro',
    'October': 'Outubro', 'November': 'Novembro', 'December': 'Dezembro'
}

# Função para traduzir o nome do mês
def traduz_mes(mes):
    return meses_pt_br.get(mes, mes)

# ------------------------------------------------------------------------

# Mapeamento de meses em inglês para português abreviados
meses_pt_br_abrv = {
    'Jan': 'Jan', 'Feb': 'Fev', 'Mar': 'Mar',
    'Apr': 'Abr', 'May': 'Mai', 'Jun': 'Jun',
    'Jul': 'Jul', 'Aug': 'Ago', 'Sep': 'Set',
    'Oct': 'Out', 'Nov': 'Nov', 'Dec': 'Dez'
}

# Função para traduzir o nome do mês abreviado
def traduz_mes_abrv(mes):
    return meses_pt_br_abrv.get(mes, mes)

# ------------------------------------------------------------------------

# Mapeamento de meses numéricos para português
meses_pt_br_num = {
    '01': 'Janeiro', '02': 'Fevereiro', '03': 'Março',
    '04': 'Abril', '05': 'Maio', '06': 'Junho',
    '07': 'Julho', '08': 'Agosto', '09': 'Setembro',
    '10': 'Outubro', '11': 'Novembro', '12': 'Dezembro'
}

# Função para traduzir o nome do mês em 'mes_ano'
def traduz_mes_ano(mes_ano):
    mes, ano = mes_ano.split('-')
    mes_traduzido = meses_pt_br_num.get(mes)
    return f"{mes_traduzido}-{ano}"

# ------------------------------------------------------------------------

# Mapeamento dos dias da semana para português
dias_da_semana_pt_br = {
    'Monday': 'Segunda-feira', 'Tuesday': 'Terça-feira', 'Wednesday': 'Quarta-feira',
    'Thursday': 'Quinta-feira', 'Friday': 'Sexta-feira', 'Saturday': 'Sábado', 'Sunday': 'Domingo'
}

def traduz_dia_semana(dia):
    return dias_da_semana_pt_br.get(dia, dia)

# ------------------------------------------------------------------------

# Mapeamento dos dias da semana para português abreviado
dias_da_semana_pt_br_abrv = {
    'Monday': 'Seg', 'Tuesday': 'Ter', 'Wednesday': 'Qua',
    'Thursday': 'Qui', 'Friday': 'Sex', 'Saturday': 'Sab', 'Sunday': 'Dom'
}

def traduz_dia_semana_abrv(dia):
    return dias_da_semana_pt_br_abrv.get(dia, dia)


# ------------------------------------------------------------------------

# Formata trimestre
def formatar_trimestre(trimestre):
    return f"T{trimestre}"

In [0]:
# Cria Dataframe com dados da dimensão calendário

# Nome da SK
nome_sk = 'sk_dim_calendar'

# Define o intervalo de datas que você deseja para sua tabela de dimensão tempo
dataInicial = to_date(lit("2000-01-01"))            # Converte as strings de data para o tipo Date
dataFinal = to_date(lit(datetime.now().strftime('%Y-%m-%d')))    # Pega a data atual

# Cria uma sequência de datas
df_datas = spark.range(1).select(explode(sequence(dataInicial, dataFinal)).alias('data'))

# Adiciona colunas necessárias
df_calendario = df_datas \
    .withColumn(nome_sk, monotonically_increasing_id()) \
    .withColumn("ano", year(col('data'))) \
    .withColumn("semana_do_ano", dayofweek(col('data'))) \
    .withColumn("dia_do_ano", dayofyear(col('data'))) \
    .withColumn("mes", month(col('data'))) \
    .withColumn("mes_ano", date_format('data','MM-yyyy')) \
    .withColumn("nome_mes_ano", date_format('data','MMM-yyyy')) \
    .withColumn("nome_mes", date_format('data','MMMM')) \
    .withColumn("nome_mes_abrv", date_format('data','MMM')) \
    .withColumn("semestre", when(col("mes") <= 6, "S1").otherwise("S2")) \
    .withColumn("trimestre", quarter(col('data'))) \
    .withColumn("nome_dia_semana", date_format(col('data'), 'EEEE')) \
    .withColumn("nome_dia_semana_abrv", date_format(col('data'), 'EEEE')) \
    .withColumn("dia", dayofmonth(col('data'))) \

# Definição e aplicação das UDFs para tradução dos nomes dos meses
traduz_mes_udf = udf(traduz_mes, StringType())
traduz_mes_abrv_udf = udf(traduz_mes_abrv, StringType())
traduz_mes_ano_udf = udf(traduz_mes_ano, StringType())
traduz_dia_semana_udf = udf(traduz_dia_semana, StringType())
traduz_dia_semana_abrv_udf = udf(traduz_dia_semana_abrv, StringType())
formatar_trimestre_udf = udf(formatar_trimestre, StringType())
    
# Aplicação da UDF para tradução dos nomes dos meses
df_calendario = df_calendario \
    .withColumn("nome_mes", traduz_mes_udf(col("nome_mes"))) \
    .withColumn("nome_mes_abrv", traduz_mes_abrv_udf(col("nome_mes_abrv"))) \
    .withColumn("nome_mes_ano", traduz_mes_ano_udf(col("mes_ano"))) \
    .withColumn("nome_dia_semana", traduz_dia_semana_udf(col("nome_dia_semana"))) \
    .withColumn("nome_dia_semana_abrv", traduz_dia_semana_abrv_udf(col("nome_dia_semana_abrv"))) \
    .withColumn("trimestre", formatar_trimestre_udf(col('trimestre')))

# Exibe o resultado
# display(df_calendario)
df_calendario.show()

+----------+---------------+----+-------------+----------+---+-------+------------+--------+-------------+--------+---------+---------------+--------------------+---+
|      data|sk_dim_calendar| ano|semana_do_ano|dia_do_ano|mes|mes_ano|nome_mes_ano|nome_mes|nome_mes_abrv|semestre|trimestre|nome_dia_semana|nome_dia_semana_abrv|dia|
+----------+---------------+----+-------------+----------+---+-------+------------+--------+-------------+--------+---------+---------------+--------------------+---+
|2000-01-01|    25769803776|2000|            7|         1|  1|01-2000|Janeiro-2000| Janeiro|          Jan|      S1|       T1|         Sábado|                 Sab|  1|
|2000-01-02|    25769803777|2000|            1|         2|  1|01-2000|Janeiro-2000| Janeiro|          Jan|      S1|       T1|        Domingo|                 Dom|  2|
|2000-01-03|    25769803778|2000|            2|         3|  1|01-2000|Janeiro-2000| Janeiro|          Jan|      S1|       T1|  Segunda-feira|                 Seg|  3

In [0]:
# Cria dataframe para a criação da dimensão
df_dimensao = df_calendario

# Insere as colunas default de dimensão
df_dimensao = df_dimensao.withColumn("row_ingestion_timestamp", current_timestamp()) 

# Ordenando as colunas
df_dimensao_select = df_dimensao.select(
     "sk_dim_calendar"
    ,"row_ingestion_timestamp"
    ,"data" 
    ,"ano" 
    ,"semana_do_ano" 
    ,"dia_do_ano"
    ,"mes" 
    ,"mes_ano" 
    ,"nome_mes_ano" 
    ,"nome_mes" 
    ,"nome_mes_abrv" 
    ,"semestre"  
    ,"trimestre" 
    ,"nome_dia_semana" 
    ,"nome_dia_semana_abrv" 
    ,"dia"
    )

display(df_dimensao_select)

sk_dim_calendar row_ingestion_timestamp data ano semana_do_ano dia_do_ano mes mes_ano nome_mes_ano nome_mes nome_mes_abrv semestre trimestre nome_dia_semana nome_dia_semana_abrv dia 25769803776 2024-04-29T12:37:23.372Z 2000-01-01 2000 7 1 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sábado Sab 1 25769803777 2024-04-29T12:37:23.372Z 2000-01-02 2000 1 2 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Domingo Dom 2 25769803778 2024-04-29T12:37:23.372Z 2000-01-03 2000 2 3 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Segunda-feira Seg 3 25769803779 2024-04-29T12:37:23.372Z 2000-01-04 2000 3 4 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Terça-feira Ter 4 25769803780 2024-04-29T12:37:23.372Z 2000-01-05 2000 4 5 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quarta-feira Qua 5 25769803781 2024-04-29T12:37:23.372Z 2000-01-06 2000 5 6 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quinta-feira Qui 6 25769803782 2024-04-29T12:37:23.372Z 2000-01-07 2000 6 7 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sexta-feira Sex 7 25769803783 2024-04-29T12:37:23.372Z 2000-01-08 2000 7 8 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sábado Sab 8 25769803784 2024-04-29T12:37:23.372Z 2000-01-09 2000 1 9 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Domingo Dom 9 25769803785 2024-04-29T12:37:23.372Z 2000-01-10 2000 2 10 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Segunda-feira Seg 10 25769803786 2024-04-29T12:37:23.372Z 2000-01-11 2000 3 11 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Terça-feira Ter 11 25769803787 2024-04-29T12:37:23.372Z 2000-01-12 2000 4 12 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quarta-feira Qua 12 25769803788 2024-04-29T12:37:23.372Z 2000-01-13 2000 5 13 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quinta-feira Qui 13 25769803789 2024-04-29T12:37:23.372Z 2000-01-14 2000 6 14 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sexta-feira Sex 14 25769803790 2024-04-29T12:37:23.372Z 2000-01-15 2000 7 15 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sábado Sab 15 25769803791 2024-04-29T12:37:23.372Z 2000-01-16 2000 1 16 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Domingo Dom 16 25769803792 2024-04-29T12:37:23.372Z 2000-01-17 2000 2 17 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Segunda-feira Seg 17 25769803793 2024-04-29T12:37:23.372Z 2000-01-18 2000 3 18 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Terça-feira Ter 18 25769803794 2024-04-29T12:37:23.372Z 2000-01-19 2000 4 19 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quarta-feira Qua 19 25769803795 2024-04-29T12:37:23.372Z 2000-01-20 2000 5 20 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quinta-feira Qui 20 25769803796 2024-04-29T12:37:23.372Z 2000-01-21 2000 6 21 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sexta-feira Sex 21 25769803797 2024-04-29T12:37:23.372Z 2000-01-22 2000 7 22 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sábado Sab 22 25769803798 2024-04-29T12:37:23.372Z 2000-01-23 2000 1 23 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Domingo Dom 23 25769803799 2024-04-29T12:37:23.372Z 2000-01-24 2000 2 24 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Segunda-feira Seg 24 25769803800 2024-04-29T12:37:23.372Z 2000-01-25 2000 3 25 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Terça-feira Ter 25 25769803801 2024-04-29T12:37:23.372Z 2000-01-26 2000 4 26 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quarta-feira Qua 26 25769803802 2024-04-29T12:37:23.372Z 2000-01-27 2000 5 27 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Quinta-feira Qui 27 25769803803 2024-04-29T12:37:23.372Z 2000-01-28 2000 6 28 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sexta-feira Sex 28 25769803804 2024-04-29T12:37:23.372Z 2000-01-29 2000 7 29 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Sábado Sab 29 25769803805 2024-04-29T12:37:23.372Z 2000-01-30 2000 1 30 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Domingo Dom 30 25769803806 2024-04-29T12:37:23.372Z 2000-01-31 2000 2 31 1 01-2000 Janeiro-2000 Janeiro Jan S1 T1 Segunda-feira Seg 31 25769803807 2024-04-29T12:37:23.372Z 2000-02-01 2000 3 32 2 02-2000 Fevereiro-2000 Fevereiro Fev S1 T1 Terça-feira Ter 1 25769803808 2024-04-29T12:37:23.372Z 2000-02-02 2000 4 33 2 02-2000 Fevereiro-2000 F

In [0]:
table_name = 'dim_calendar'
spark.sql('USE olist')
spark.sql(f'DROP TABLE IF EXISTS dim_calendar')
df_dimensao_select.write.format("delta").mode('overwrite').saveAsTable(table_name)